In [ ]:
#CELL 1
#@title Keep this tab alive to prevent Colab from disconnecting you
#@markdown Press play on the music player that will appear below:
%%html
<audio src="https://oobabooga.github.io/silence.m4a" controls>

In [ ]:
from urllib.parse import urlsplit
from pathlib import Path
import pathlib
import os
import re
import tarfile
import threading
import random
import time
import math
import pip
from google.oauth2.service_account import Credentials
import hashlib
import gspread

###/@todo:checks via os.path.getsize()

# @markdown # MODEL
# @markdown #### paste here **link to the huggingface.co** model, or select one of the popular model from the dropdown:
input_model_string = "https://huggingface.co/Undi95/Amethyst-13B-GGUF/resolve/main/Amethyst-13B.q4_K_S.gguf" # @param ["https://huggingface.co/QMB15/mythomax-L2-13B-4.625bit-exl2", "https://huggingface.co/TheBloke/MythoMax-L2-13B-GPTQ", "https://huggingface.co/TheBloke/MythoMax-L2-13B-GGUF/resolve/main/mythomax-l2-13b.Q4_K_M.gguf", "https://huggingface.co/TheBloke/MythoMax-L2-13B-GGUF/blob/main/mythomax-l2-13b.Q6_K.gguf", "https://huggingface.co/Kotokin/MLewd-L2-13B-v2-1-GPTQ", "https://huggingface.co/TheBloke/MLewdBoros-L2-13B-GPTQ", "https://huggingface.co/Undi95/MLewdBoros-LRPSGPT-1Char-13B-GGUF/resolve/main/MLewdBoros-LRPSGPT-1Char-13B.q4_K_S.gguf", "https://huggingface.co/Undi95/MLewdBoros-LRPSGPT-1Char-13B-GGUF/resolve/main/MLewdBoros-LRPSGPT-1Char-13B.q6_K.gguf", "https://huggingface.co/ludis/tsukasa-13b-qlora-limarp-gptq", "https://huggingface.co/ludis/tsukasa-13b-qlora-limarp-gguf/resolve/main/tsukasa-13b-qlora-limarp-q4_k_m.gguf", "https://huggingface.co/ludis/tsukasa-13b-qlora-limarp-gguf/resolve/main/tsukasa-13b-qlora-limarp-q5_k_m.gguf", "https://huggingface.co/TheBloke/Amethyst-13B-Mistral-GPTQ", "https://huggingface.co/Undi95/Amethyst-13B-GGUF/resolve/main/Amethyst-13B.q4_K_S.gguf","https://huggingface.co/Undi95/Amethyst-13B-GGUF/resolve/main/Amethyst-13B.q6_K.gguf", "https://huggingface.co/TheBloke/Mistral-7B-v0.1-GPTQ", "https://huggingface.co/TheBloke/Mistral-7B-v0.1-GGUF/resolve/main/mistral-7b-v0.1.Q8_0.gguf", "https://huggingface.co/tekkithorse/GPT-J-6B-PNY-GGML/resolve/main/ggml-q4_1.bin", "https://huggingface.co/Nikolai1902/LL2-13B-DesuMLP-QLORA-GGML/resolve/main/ggml-LLama%202%2013B%20mlparchive-Q4_K_S.bin", "https://huggingface.co/Nikolai1902/LL2-13B-DesuMLP-QLORA-GGML/resolve/main/ggml-LLama%202%2013B%20mlparchive-Q5_K_M.bin", "https://huggingface.co/Nikolai1902/LL2-13B-FIMFiction-QLORA-GGML/resolve/main/ggml-LLama%202%20FIMFiction%20V1-13B-Q4_K_S.bin", "https://huggingface.co/Nikolai1902/LL2-13B-FIMFiction-QLORA-GGML/resolve/main/ggml-LLama%202%20FIMFiction%20V1-13B-Q5_K_M.bin"] {allow-input: true}
# @markdown ##### the last five models in the list are pony-themed models.
# @markdown acceptable formats:
# @markdown * *(GPTQ / EXL2 - link to the repo)* https://huggingface.co/ludis/tsukasa-13b-qlora-limarp-gptq
# @markdown * *(GPTQ / EXL2 - link to the tree/branch)* https://huggingface.co/QMB15/mythomax-13B-8.13bit-MAX-exl2/tree/main
# @markdown * *(GGUF / GGML - link to the exact file)* https://huggingface.co/Undi95/MLewdBoros-L2-13B-GGUF/blob/main/MLewdBoros-L2-13B.q5_K_M.gguf
# @markdown ***

# @markdown # CONTEXT
# @markdown ### max context
# @markdown #### select **max context** size (*--alpha_value* will be adjusted). set to "**0**" and notebook will **try** to detect appropriate max content automatically
# @markdown kobald.cpp accepts only the following values: 512, 1024, 2048, 3072, 4096, 6144, 8192, 12288, 16384
input_model_context = 0 # @param {type:"slider", min:0, max:16384, step:512}

# @markdown ### freeway
# @markdown #### here you can set any **max content** and **alpha_value** you want. set to "**0**" to disable those options
input_model_free_context = 0 # @param {type:"number"}
input_model_free_alpha_value = 0 # @param {type:"number"}
# @markdown ***

# @markdown # LOADER / BACKEND
# @markdown #### if you want to launch the model via specific **loader / backend** then pick it here, otherwise left to "**autodetect**"
# @markdown notebook supports [kobold.cpp](https://github.com/LostRuins/koboldcpp) (GGUF / GGML) [oobabooga](https://github.com/oobabooga/text-generation-webui) (GPTQ / EXL2 / GGUF)
input_model_loader = "autodetect" # @param ["autodetect", "koboldcpp", "exllamav2", "exllamav2_hf", "autoawq", "exllama", "exllama_hf", "autogptq", "gptq-for-llama", "llamacpp", "llamacpp_hf", "ctransformers"]
# @markdown explanation:
# @markdown * koboldcpp : GGUF / GGML
# @markdown * exllamav2 : EXL2
# @markdown * exllamav2_hf : EXL2 + extra samplers
# @markdown * exllama : GPTQ
# @markdown * exllama_hf : GPTQ + extra samplers
# @markdown * autogptq : GPTQ
# @markdown * gptq-for-llama : GPTQ (outdated, better use autogptq)
# @markdown * llamacpp : GGUF
# @markdown * llamacpp_hf : GGUF + extra samplers
# @markdown * ctransformers : GGML
# @markdown ***

# @markdown # OPTIONAL MODEL SETTINGS
# @markdown ### format
# @markdown #### if you know **model's format**, then set it here, otherwise pick "**autodetect**" and notebook will try to detect it automatically
input_model_format = "autodetect" # @param ["autodetect", "EXL2", "GPTQ", "GGUF", "GGML"]
# @markdown ### parameters
# @markdown #### if you know **model's parameters / beaks**, then set it here, otherwise type "**0**" and notebook will try to detect it automatically
input_model_beaks = 0 # @param {type:"number"}
# @markdown ### quantz (for GGUF / GGML)
# @markdown #### if you know **model's quantz**, for set it here, otherwise pick "**autodetect**" and notebook will try to detect it automatically
input_model_quantz = "autodetect" # @param ["autodetect", "q2_k", "q3_k_s", "q3_k_m", "q3_k_l", "q4_0", "q4_k_s", "q4_1", "q4_k_m", "q5_0", "q5_1", "q5_k_s", "q5_k_m", "q6_k", "q8_0", "f16"]
# @markdown ### bits (for EXL2)
# @markdown #### if you know **model's bits**, then set it here, otherwise type "**0**" and notebook will try to detect it automatically
input_model_bits = 0 # @param {type:"number"}
# @markdown ***

# @markdown # LORA
# @markdown ### custom LoRA
# @markdown #### paste here **link to the huggingface.co** LoRA, or left empty if don't need them
# @markdown can specify multiply LoRAs via comma, ex. Link1, Link2
input_lora_string = "" # @param {type:"string"}
# @markdown ### pony LoRAs (GPTQ only)
# @markdown #### will apply one of the /mlp/ LoRAs to the model
input_lora_pony = "none" # @param ["none", "FIMFarchive-v1", "desu-/mlp/-v1"]
# @markdown description:
# @markdown * FIMFarchive-v1 - dataset of fanfics from FIMfiction archive
# @markdown * desu-/mlp/-v1 - dataset of /mlp/ posts, including greentext
# @markdown ***

# @markdown # KOBOLD.CPP
# @markdown ### kobold.cpp version
# @markdown #### select what version of kobold.cpp you want to use:
# @markdown * "latest" : will download and patch the latest version of kobold.cpp. it will take ~4 minutes
# @markdown * "1.43" : already patched version done by [kalomaze](https://github.com/kalomaze/koboldcpp/releases/latest). it will take ~10 seconds
# @markdown * "1.44.2" : already patched version done by [me](https://github.com/raremewB/koboldcpp/releases/latest). it will take ~10 seconds
# @markdown * "1.46.1" : ditto ^
input_kobold_version = "1.46.1" # @param ["latest", "1.46.1", "1.44.2", "1.43"]
# @markdown ### --smartcontext
# @markdown #### launch kobold.cpp with --smartcontext flag to speed up performance on huge prompts, but returns empty responses sometimes
input_kobold_smartcontext = False # @param {type:"boolean"}
# @markdown ### --stream
# @markdown #### launch kobold.cpp with --stream flag to allow streaming
# @markdown (the very latest kobold.cpp deprecated that flag and always uses streaming; oobabooga has it enabled by default)
input_kobold_stream = True # @param {type:"boolean"}
# @markdown ### --gpulayers
# @markdown #### change the number of layers to be sent in VRAM. usually you don't need to tweak it and it always shall be "43"
# @markdown (that option affects llamacpp in oobabooga too, which calls it --n-gpu-layers)
input_flag_gpulayers = "43" # @param ["43", "42", "41", "40"]
# @markdown ### use CPU only
# @markdown #### launch kobold.cpp in CPU-only mode. **the performance will be extremely slow!**
input_kobold_usecpu = False # @param {type:"boolean"}
# @markdown ***

# @markdown # OOBABOOGA
# @markdown ### --verbose
# @markdown #### launch oobabooga with --verbose flag to force it store logs into Colab console
input_ooba_logs = False # @param {type:"boolean"}
# @markdown ### --cfg-cache
# @markdown #### launch oobabooga with --cfg-cache flag to make it use the negative prompts
# @markdown **warning: the VRAM usage has been doubled**
input_ooba_cfg = False # @param {type:"boolean"}
# @markdown ### use Gradio interface
# @markdown #### use Gradio frontend (open `*.gradio.live` in browser)
# @markdown #### because anyone is able to open the link - set your random username and pw:
input_ooba_gradio = False # @param {type:"boolean"}
input_ooba_gradio_name = "anon" # @param {type:"string"}
input_ooba_gradio_pw = "PlapPlap1234" # @param {type:"string"}
# @markdown ***

# @markdown # PONIES
# @markdown add a bit of ponies into your console (doesn't affect models in any way)
input_ponies = True # @param {type:"boolean"}
# @markdown ***

# @markdown # ANALYTICS
# @markdown #### anonymously submit download data (model name and hash)
# @markdown the data is collected only for measuring models' usage/popularity and publicly available in [Google Spreadsheet](https://docs.google.com/spreadsheets/d/1zR1JAg0eRLFme7CqTDJG5xPHpYE-H169ymOWXOwXzok/edit?usp=sharing). the code and Spreadsheet are done by [@kalomaze](https://github.com/kalomaze)
input_analytics = False # @param {type:"boolean"}
# @markdown ***

###################################
### CREDITS
###################################
# @ anon who made pony-related notebook - https://colab.research.google.com/drive/1Un02h4uQN6zLlgL3zmMOeyce9ICEA3qO)
# @ Colab ooba anon - https://files.catbox.moe/kd79da.ipynb
# @ kalomaze - https://github.com/kalomaze/
# @ LostRuins from koboldcpp - https://github.com/LostRuins
# @ freellamas anon - https://rentry.org/freellamas
# @ colabfreellamas anon - https://rentry.org/colabfreellamas

###################################
### INPUT PRE-PROCESS
###################################
# brief sanitize of user's inputs
# that 'or 0' thing converts all falsey values into 0 (None -> 0, False -> 0...)
input_model_context = int(input_model_context)
input_model_free_context = int(input_model_free_context or 0)
input_model_free_alpha_value = float(input_model_free_alpha_value or 0.0)
input_model_loader = str(input_model_loader).lower()
input_model_format = str(input_model_format).lower()
input_model_beaks = int(input_model_beaks or 0)
input_model_quantz = str(input_model_quantz).lower()
input_model_bits = int(input_model_bits or 0)
input_lora_string = str(input_lora_string)
input_lora_pony = str(input_lora_pony)
input_kobold_version = str(input_kobold_version).lower()
input_kobold_smartcontext = bool(input_kobold_smartcontext)
input_kobold_stream = bool(input_kobold_stream)
input_flag_gpulayers = int(input_flag_gpulayers or 43)
input_kobold_usecpu = bool(input_kobold_usecpu)
input_ooba_logs = bool(input_ooba_logs)
input_ooba_cfg = bool(input_ooba_cfg)
input_ooba_gradio = bool(input_ooba_gradio)
input_ooba_gradio_name = str(input_ooba_gradio_name)
input_ooba_gradio_pw = str(input_ooba_gradio_pw)
input_ponies = bool(input_ponies)

###################################
### GLOBALS
###################################
#global paths to reuse in code
PATH = {
  "base": "/content/",
  "main": "/content/colabMain/",
  "temp": "/content/colabTemp/",
  "ooba": "/content/colabMain/text-generation-webui/",
  "ooba_start": "/content/colabMain/text-generation-webui/server.py",
  "kobold": "/content/colabMain/koboldcpp/",
  "kobold_start": "/content/colabMain/koboldcpp/koboldcpp.py",
  "kobold_tar": "/content/koboldcpp.tar.gz",
  "disk_base": "/content/drive/MyDrive/",
  "disk": "/content/drive/MyDrive/colabMain/",
  "cloud_nohup": "/content/nohup.out",
  "cloud_deb": "/content/cloudflared-linux-amd64",
  "fix": "/content/fix/",
  "sheet_done": "/content/done.txt",
  "sheet_start": "/content/peppy-generator-388800-07722f17a188.json"
}

#info about Model
MODEL = set()
LORA = set()


###################################
### HELPERS
###################################
def log(msg, lvl="note"):
  #logger with custom colors. cool kids' print()
  MAP_colors = {
      "note": "\033[0m",                # norm
      "pony": "\033[95m",               # purple            --pony
      #"pony": "\033[105m\033[97m",     # annoying purple   --pony
      "sect": "\n\033[104m\033[97m",    # blue background   --section
      "info": "\033[103m",              # yellow background --info
      "log":  "\033[103m",              # ^same
      "bad": "\033[101m\033[97m",       # red background    --very important
      "green": "\033[92m"               # greentext         --for one dumb joke
  }
  print(f"{MAP_colors[lvl.lower()]}{msg}\033[0m")

def get_element(arr, index, default):
  #get array[index] and assign default if undefined (out-of-bounds)
  arr_dict = dict.fromkeys(range(len(arr)), None)
  arr_dict.update({i: val for i, val in enumerate(arr)})
  return arr_dict.setdefault(index, default)


###################################
### PONIES
###################################
def ponies_set():
  #you don"t ask MLP-ways. yes, not all of them are ponies but noone likes the term "everycreature"
  pony_names = ("Moondancer", "Applejack", "Rarity", "Fluttershy", "Twilight Sparkle", "Rainbow Dash", "Pinkie Pie", "Princess Luna", "Princess Celestia", "Princess Cadance", "Shining Armor", "Flurry Heart", "Nightmare Moon", "Daybreaker", "Nightmare Rarity", "The Great and Powerful Trixie", "Starlight Glimmer", "Sunburst", "Sunset Shimmer", "Lyra Heartstrings", "Bon Bon", "Octavia Melody", "Vinyl Scratch", "Derpy Hooves", "Doctor Whooves", "Carrot Top", "Roseluck", "Lily Valley", "Daisy", "Big Macintosh", "Apple Bloom", "Scootaloo", "Sweetie Belle", "Snails", "Snips", "Diamond Tiara", "Silver Spoon", "Twist", "Babs Seed", "Rumble", "Pipsqueak", "Thunderlane", "Soarin", "Spitfire", "Lightning Dust", "Queen Chrysalis", "Discord", "King Sombra", "Cozy Glow", "Lord Tirek", "Opaline Arcana", "Sonata Dusk", "Adagio Dazzle", "Aria Blaze", "Tempest Shadow", "Sci-Twi", "Flash Sentry", "Wallflower Blush", "Indigo Zap", "Lemon Zest", "Sour Sweet", "Sugarcoat", "Sunny Flare", "Izzy Moonbow", "Sunny Starscout", "Pipp Petals", "Zipp Storm", "Hitch Trailblazer", "Misty Brightdawn", "Maud Pie", "Marble Pie", "Limestone Pie", "Cheerilee", "Berry Punch", "Zecora", "Daring Do", "Coco Pommel", "Gilda", "Princess Ember", "Thorax", "Gabby", "Autumn Blaze", "Smolder", "Gallus", "Silverstream", "Ocellus", "Yona", "Sandbar", "Braeburn", "Caramel", "Minuette", "Button Mash", "Dinky Hooves", "Cheese Sandwich", "Prince Blueblood", "Fleur-de-lis", "Fancypants", "Cloudchaser", "Nurse Redheart", "Moondancer", "Bulk Biceps", "Mayor Mare", "Sugar Belle", "Pear Butter", "Coloratura", "Tree Hugger", "Lotus", "Aloe", "Pound Cake", "Pumpkin Cake", "Photo Finish", "Amethyst Star", "Zephyr Breeze", "Luster Dawn", "Spike")
  pony_actions = ("ministrates", "audible pops", "has turned into pet", "is turned into pet by", "throws ball into court of", "gives choices to", "does not bite", "looks with half-lidded eyes at", "worries bottom lip while looking at", "has an arousal pooling in belly because of", "takes pleasure with", "kisses kiss-bruised lips of", "bruisingly kisses", "is yours to take,", "is wanton for", "ministrates", "has reckless abandon because of", "'s hooves turning white at sight of", "grins wickedly at", "has fiery red mane, chestnut eyes and long lashes while looking at", "'s propriety be damned! because of", "'s pupils blown wide with pleasure at sight of", "tongue darts out at", "grasps the chin of", "forced to meet gaze of", "bites the ear of", "hollows the cheeks at", "'s inner walls clenching around nothing around", "has a puckered hole, and that bitch loves it -", "biting the lips while thinking of", "has slick folds, soon will be plapped by", "'s heart, body and soul belong to", "believes that the night is still young with", "plaps-plaps", "is got pregnant by", "said ahh-ahh-mistress to", "hugs", "kisses", "cuddles", "nuzzles")

  while input_ponies:
    # Claudenations = Claude + combinations
    log(f"\n{random.choice(pony_names)} {random.choice(pony_actions)} {random.choice(pony_names)}", "pony")
    #can be random like time.sleep(random.randint(15, 30)) but t-b-h fixed time is better
    time.sleep(20)


###################################
### DOWNLOADER - MODEL
###################################
def depend_aria():
  #install aria2c to download stuff; install only if not present in system
  if (not os.path.exists("/usr/bin/aria2c")):
    log("...[aria2c] aria2c is NOT present in system, installing", "info")
    #apt is faster than apt-get kek: (3.1 2.4 2.2 2.3 2.9)s vs (4.3 5.4 4.0 5.3 5.1)s
    !sudo apt install aria2 -y >/dev/null 2>&1

def depend_kobold_cloudflare():
  #install cloudflare for kobold.cpp; install only if not present in system
  if not os.path.exists(PATH["cloud_deb"]):
    log("...[cloudflare] Cloudflare is NOT present in system, installing", "info")
    #can be done with urllib.request or requests but it works with !wget and I don't want to use aria2c here
    !wget -q https://github.com/cloudflare/cloudflared/releases/latest/download/cloudflared-linux-amd64 {PATH["base"]}
    #changing file permissions
    os.chmod(PATH["cloud_deb"], 0o755)

  #nohup.out stores info from the launched Cloudflare
  #we deleting it to prevent outputting double-links into console and confuse users
  if os.path.exists(PATH["cloud_nohup"]):
    log("...[cloudflare] nohup.out from the previous instance was detected, deleting")
    os.remove(PATH["cloud_nohup"])

  log("...[cloudflare] launching Cloudflare and waiting for an answer")
  !nohup {PATH["cloud_deb"]} tunnel --url http://localhost:5001 &
  while True:
    #looping until nohup.out have nessecary info then breaking loop
    #since it is running in Thread, we don't care about how long that loop takes
    with open(PATH["cloud_nohup"]) as o:
      if ("connIndex=" in o.read()):
        break
    time.sleep(1)

def download_aria(download_link, destination=PATH["temp"], filename=False):
  # download the file via aria2c. ugly and dirty but it works
  log(f"~~~ downloading / link: {download_link} destination: {destination} filename: {filename}", "log")
  aria = f"aria2c --console-log-level=error -c -x 16 -s 16 -k 1M --allow-overwrite='true' --summary-interval=5 {download_link} -d {destination}{' -o ' + filename if filename else ''} 2>&1 | grep -Ev 'Redirecting'"
  !$aria

def download_git(download_link, destination=PATH["temp"], branch="main"):
  #first we build the list of files for the model, we don"t download anything yet
  !git lfs install --skip-smudge && export GIT_LFS_SKIP_SMUDGE=1 && git clone {download_link} {destination} --branch {branch}

  #then we list thry the pool of files and download them one by one
  #we skip *.md and *.txt files and other dummy files (don't download them), and delete .git folder
  os.system(f'rm -rf {destination}/.git')
  for filename in os.listdir(destination):
    if filename.endswith(tuple([".md", ".txt"])) or filename.lower() in ["pytorch_model.bin.index.json", "training_args.bin", "trainer_state.json", "all_results.json", "eval_results.json", ".gitattributes", "train_results.json", "license", "notice", "readme", "use_policy"]:
      continue
    download_aria(f"{download_link}/{'raw' if filename.endswith('.json') else 'resolve'}/{branch}/{filename}", destination, filename)

def check_if_exists_and_download_model():
  #first, check whether the downloaded files are present in system
  #for GGUF/GGML - check whether file exists (downloaded)
  #for GPTQ/EXL2 - check whether folder exists (downloaded) and has content inside
  if (MODEL["mode"] == "file" and not os.path.isfile(MODEL["path_pointer"])):
    log("...[model] model is NOT present in system, downloading", "info")
    download_aria(MODEL["link_pointer"], PATH["temp"], MODEL["filename"])
  elif (MODEL["mode"] == "folder" and not (os.path.exists(MODEL["path_pointer"]) and len(os.listdir(MODEL["path_pointer"])) > 0)):
    log("...[model] model is NOT present in system, downloading", "info")
    download_git(MODEL["link_pointer"], MODEL["path_pointer"], MODEL["branch"])
  else:
    log("...[model] model is already downloaded")


###################################
### BACKEND
###################################
def download_backend_ooba():
  #download oobabooga backend for GPTQ / EXL2 / GGUF files
  #clone from github and installing requirement
  #installing version 1.6.1 because EXL2 suppport on latest commits is broken
  !git clone -b 1.6.1 https://github.com/oobabooga/text-generation-webui {PATH["ooba"]}
  !pip install -r {PATH["ooba"]}requirements.txt --no-input -qq
  #flash-attn breaks EXL2 in Colab so we uninstall it
  !pip uninstall -y flash-attn --no-input -qq

  #installing Cloudflare for oobabooga. it will launch Cloudflare on its own
  !pip install flask_cloudflared --no-input -qq
  !wget -q https://github.com/cloudflare/cloudflared/releases/latest/download/cloudflared-linux-amd64.deb
  !apt install ./cloudflared-linux-amd64.deb
  !rm cloudflared-linux-amd64.deb

  #required for GGUF models
  download_git("https://huggingface.co/oobabooga/llama-tokenizer", f"{PATH['temp']}llama-tokenizer", "main")

def download_backend_kobold():
  #download kobold.cpp backend for GGUF / GGML files
  def download_kobold_tarball(link):
    #code idea is borrowed from kalomaze's Colab
    #download tarfile and unpack it
    #we use wget here because aria2c might be busy with downloading the models/lora
    !wget -q {link} {PATH["kobold_tar"]}
    tar = tarfile.open(PATH['kobold_tar'], 'r:gz')
    tar.extractall(path=PATH['main'])

  def download_kobold_latest():
    #download the latest version of kobold.cpp from github and patch it to use CUDA
    !git clone https://github.com/LostRuins/koboldcpp {PATH["kobold"]}
    !make -C {PATH["kobold"]} LLAMA_CUBLAS=1

  KOBOLD_VERSIONS = {
    "1.43": "https://github.com/kalomaze/koboldcpp/releases/download/Colab/koboldcpp.tar.gz",
    "1.44.2": "https://github.com/raremewB/koboldcpp/releases/download/Colab/koboldcpp.tar.gz",
    "1.46.1": "https://github.com/raremewB/koboldcpp/releases/download/1461/koboldcpp.tar.gz"
  }

  if input_kobold_version in KOBOLD_VERSIONS:
    log(f"...[backend] user has selected to install kobold.cpp {input_kobold_version} from tar, it will take ~10 seconds")
    download_kobold_tarball(KOBOLD_VERSIONS[input_kobold_version])
  else:
    log(f"...[backend] user has selected to install the latest version of kobold.cpp, it will take ~4 minutes")
    download_kobold_latest()

def check_if_exists_and_download_ooba():
  if (not os.path.exists(PATH["ooba_start"])):
    log("...[backend] oobabooga is NOT present in system, installing", "info")
    download_backend_ooba()
  else:
    log("...[backend] oobabooga is already installed")

def check_if_exists_and_download_kobold():
  if (not os.path.exists(PATH["kobold_start"])):
    log("...[backend] kobold.cpp is NOT present in system, installing", "info")
    download_backend_kobold()
  else:
    log("...[backend] kobold.cpp is already installed")


###################################
### FUNCTION - CLEANERS
###################################
def clean_string(text, lowercase=False):
  #remove trailing spaces, optionally convert into lowercase
  if lowercase:
    return text.strip().lower()
  return text.strip()

def clean_link(link):
  #remove www. from the link, replace http with https://, remove trailing slash, raise warning if domain isn"t hf.co
  link = clean_string(link)

  parts = urlsplit(link)
  if (not all([parts.scheme, parts.netloc])):
    log(f"{link} is a broken url according to urlsplit() - probably missing https:// protocol; will fix it but issues may happen", "info")
    parts = urlsplit(f"https://{link}")

  if (parts.netloc.replace("www.","").lower() not in ["huggingface.co", "hf.co"]):
    log(f"{link} is not from huggingface.co or hf.co domains; issues will happen", "bad")

  return f"https://huggingface.co{parts.path.rstrip('/')}"


###################################
### FUNCTION - PARSERS
###################################
def gguf_ggml_fixer(link, branch):
  # if user passed link to GGUF / GGML model without full path to the file:
  # .../TheBloke/MythoMax-L2-13B-GGUF/tree/main instead of .../TheBloke/MythoMax-L2-13B-GGUF/blob/main/mythomax-l2-13b.Q5_K_M.gguf
  # then that function will fix it by browsing thry model's files and deducing the proper name

  # leftover folder from the previous time we launched that function. deleting it before git
  if os.path.exists(PATH["fix"]): os.system(f"rm -rf {PATH['fix']}")

  !git lfs install --skip-smudge && export GIT_LFS_SKIP_SMUDGE=1 && git clone {link} {PATH["fix"]} --branch {branch}
  #quantz in order of preference
  #we go thry quantz firsthand because filelist is in random order
  for quant in ["q6_k", "q5_k_m", "q5_k", "q4_k_m", "q4_k", "q3_k_l", "q3_k_m", "q3_k", "q5_1", "q5_0", "q4_1", "q4_0", "q2_k", "q8_0", "f16"]:
    for filename in os.listdir(f"{PATH['fix']}"):
      if quant in filename.lower():
        return filename
  return "adapter_model.bin"

def detect_format(text):
  #read the text and detect model format. return "unknown" if cannot detect model this way
  #@todo: maybe read from the other files if "unknown", like from config.json? meh idea overall
  formats = ["exl2", "awq", "gptq", "gguf", "ggml"]
  for format in formats:
    if format in text:
      return format
  return "unknown"

def detect_backend(format="unknown"):
  #sets the default backend
  backends = {
    "exl2": "exllamav2_hf",
    "awq": "autoawq",
    "gptq": "exllama_hf",
    "gguf": "koboldcpp",
    "ggml": "koboldcpp",
    "unknown": "exllama_hf"
  }
  return backends[format]

def detect_mode(format="unknown"):
  #sets what we shall download from hf - the whole folder with models (GPTQ, EXL2) or a single file (GGUF, GGML)
  modes = {
    "exl2": "folder",
    "awq": "folder",
    "gptq": "folder",
    "gguf": "file",
    "ggml": "file",
    "unknown": "folder"
  }
  return modes[format]

def detect_beak(text):
  #read the text and detect beaks (parameters)
  #13b, 7b, and 20b for first to end the loop faster
  beaks = ["13b", "7b", "20b", "140b", "70b", "65b", "33b", "30b", "6b", "3b", "1b"]
  for beak in beaks:
    if beak in text:
      return int(beak.replace("b",""))

  #part above covers all major cases. ideally that regex shall never be called
  match_re = re.search(r"[\-\.\_ ](\d+)[Bb][\-\.\_ ]", text)
  if match_re:
    return int(match_re.group(1))
  return "unknown"

def detect_quantz(text):
  #read the text and detect quantz. needed only for GGUF/GGML
  quantz = ["q2_k", "q3_k_s", "q3_k_m", "q3_k_l", "q4_0", "q4_k_s", "q4_1", "q4_k_m", "q5_0", "q5_1", "q5_k_s", "q5_k_m", "q6_k", "q8_0", "f16"]
  for quant in quantz:
    if (quant in text):
      # converts text quantz into number ('q4_k_m' -> 4, 'q5_k_m' -> 5)
      return quant, int(re.search(r"[qf](\d+)", quant).group(1))
  return "unknown", "unknown"

def detect_bit(text):
  #read the text and detect bits. very dirty and ugly. needed only for EXL2
  match_re = re.search(r"([\.\d]+)(bit|bpw)s?", text)
  if match_re:
    return float(match_re.group(1))
  return "unknown"

def parse_link(link):
  global MODEL

  #read the link and parse into components with defaults
  #it can be improved into more Pythonic code, but honestly - it works and bullet-proof: why shall one bother?
  #get_element reads array"s element and assigns a default one if undefined
  parts = clean_link(link).split("/")
  protocol = get_element(parts, 0, "https:")
  empty = get_element(parts, 1, "")
  domain = get_element(parts, 2, "huggingface.co")
  author = get_element(parts, 3, "ludis")
  repo = get_element(parts, 4, "tsukasa-13b-qlora-limarp-gptq") # :3
  tree = get_element(parts, 5, "tree")
  branch = get_element(parts, 6, "main")
  filename = get_element(parts, 7, "adapter_model.bin") #set default to adapter_model.bin because couldn't think of better one

  link_main = f"https://huggingface.co/{author}/{repo}"
  link_repo = f"{link_main}/tree/{branch}"
  link_file = f"{link_main}/blob/{branch}/{filename}"
  link_file_download = f"{link_main}/resolve/{branch}/{filename}"

  #all parsing is done via the full link
  format = detect_format(clean_string(link_file, True))
  backend = detect_backend(format)
  mode = detect_mode(format)
  if (format in ["gguf", "ggml"] and filename == "adapter_model.bin"):
    filename = gguf_ggml_fixer(link_main, branch)
    link_file = f"{link_main}/blob/{branch}/{filename}"
    link_file_download = f"{link_main}/resolve/{branch}/{filename}"

  link_file_process = clean_string(link_file_download, True)
  beaks = detect_beak(link_file_process)
  quantz, quantz_num = detect_quantz(link_file_process) #@todo: force only GGUF/GGML for that? and EXL2 for bits?
  bits = detect_bit(link_file_process)

  #messy but works
  if (mode == "folder"):
    pointer = repo
    link_pointer = link_main
  elif (mode == "file"):
    pointer = filename
    link_pointer = link_file_download
  path_pointer = f"{PATH['temp']}{pointer}"

  MODEL = {
    "author": author,
    "repo": repo,
    "branch": branch,
    "filename": filename,
    "link_raw": link,
    "link_main": link_main,
    "link_repo": link_repo,
    "link_file": link_file,
    "link_file_download": link_file_download,
    "format": format,
    "backend": backend,
    "mode": mode,
    "beaks": beaks,
    "quantz": quantz,
    "quantz_num": quantz_num,
    "bits": bits,
    "pointer": pointer,
    "path_pointer": path_pointer,
    "link_pointer": link_pointer
  }
  return MODEL

def proc_model_details(item):
  for x in item:
    log(f"  {x} -- {item[x]}")

def proc_model_notes(elem):
  log("::: NOTIFICATIONS :::", "sect")
  global MODEL

  ########
  #model format tests
  #each of tests has the very same first tests - we check whether user set something in form, and apply it
  #if user didn't set option and script cannot apply it either, then set some default setting
  #I know that it can be optimized with some dictionary but I prefer having ir robust and visual like that
  if (input_model_format and input_model_format != "autodetect"):
    if (MODEL["format"] == "unknown"):
      log(f"script couldn't detect the _format of model_, but user set - {input_model_format.upper()}; will follow user's choice", "log")
    elif (MODEL["format"] == input_model_format):
      log(f"script has detected the following _format of model_ - {MODEL['format'].upper()}, and user picked the same _format of model_ too")
    elif (MODEL["format"] != input_model_format):
      log("script has detected the following _format of model_ - {MODEL['format'].upper()}, but user picked - {input_model_format.upper()}; will follow user's choice", "log")
    MODEL["format"] = input_model_format
  #after the previous checks format shall never be unknown. but I still include that failsafe
  if (MODEL["format"] == "unknown"):
    log(f"script couldn't detect the _format of model_ and user didn't set it either; will use GPTQ and hope for the best", "bad")
    MODEL["format"] = 'gptq'
  #then some notifications on specific formats
  if (MODEL["format"] == "awq"):
    log("script has detected AWQ format which is a new format and lots of options are currently unavailable for it, like LoRAs")
  elif (MODEL["format"] == "exl2"):
    log("script has detected EXL2 format which is a new format and lots of options are currently unavailable for it, like LoRAs")
  elif (MODEL["format"] == "ggml"):
    log("script has detected GGML format which is outdated; use koboldcpp for it or better switch to GGUF format")


  ########
  #loader tests
  if (input_model_loader and input_model_loader != "autodetect"):
    if (MODEL["backend"] == "unknown"):
      log(f"script couldn't detect the _loader_, but user set - {input_model_loader}; will follow user's choice", "log")
    elif (MODEL["backend"] == input_model_loader):
      log(f"script has detected the following _loader_ - {MODEL['backend']}, and user picked the same _loader_ too")
    elif (MODEL["backend"] != input_model_loader):
      log(f"script has detected the following _loader_ - {MODEL['backend']}, but user picked - {input_model_loader}; will follow user's choice", "log")
    MODEL["backend"] = input_model_loader
  if (MODEL["backend"] == "unknown"):
    log("script couldn't detect the _loader_ and user didn't set it either; will use exllama_hf and hope for the best", "bad")
    MODEL["backend"] = 'exllama_hf'
  #read whatever user picked and report when he picked unoptimal/wrong loader
  #could be done via dictionary, but whatever @todo
  if (MODEL["format"] == "exl2"):
    if (not MODEL["backend"] in ["exllamav2_hf", "exllamav2"]):
      log(f"user is loading EXL2 format via {MODEL['backend']} ! use exllamav2_hf or exllamav2 instead!", "bad")
    elif (MODEL["backend"] != "exllamav2_hf"):
      log(f"script's default option for EXL2 format is exllamav2_hf, but user picked - {MODEL['backend']}; will follow user's option", "log")
  elif (MODEL["format"] == "gptq"):
    if (not MODEL["backend"] in ["exllama_hf", "exllama", "autogptq", "gptq-for-llama"]):
      log(f"user is loading GPTQ format via {MODEL['backend']} ! use exllama_hf or exllama or autogptq or gptq-for-llama instead!", "bad")
    elif (MODEL["backend"] != "exllama_hf"):
      log(f"script's default option for GPTQ format is exllama_hf, but user picked - {MODEL['backend']}; will follow user's option", "log")
  elif (MODEL["format"] == "gguf"):
    if (not MODEL["backend"] in ["koboldcpp", "llamacpp_hf", "llamacpp"]):
      log(f"user is loading GGUF format via {MODEL['backend']} ! use koboldcpp or llamacpp_hf or llamacpp instead! ", "bad")
    elif (MODEL["backend"] != "koboldcpp"):
      log(f"script's default option for GGUF format is koboldcpp, but user picked - {MODEL['backend']}; will follow user's option", "log")
  elif (MODEL["format"] == "ggml"):
    #for GGML the very first notification we must do is inform to not do GGML via llamacpp / llamacpp_hf
    if (MODEL["backend"] in ["llamacpp_hf", "llamacpp"]):
      log(f"user is trying to load GGML format via {MODEL['backend']} - they do not support GGML anymore! use koboldcpp or ctransformers instead! ", "bad")
    elif (not MODEL["backend"] in ["koboldcpp", "ctransformers"]):
      log(f"user is loading GGML format via {MODEL['backend']} ! use koboldcpp or ctransformers instead! ", "bad")
    elif (MODEL["backend"] != "koboldcpp"):
      log(f"script's default option for GGML format is koboldcpp, but user picked - {MODEL['backend']}; will follow user's option", "log")
  elif (MODEL["format"] == "awq"):
    if (MODEL["backend"] != "autoawq"):
      log(f"user is loading AWQ format via {MODEL['backend']} ! use autoawq instead! ", "bad")


  ########
  #loader tests
  if (input_model_beaks and input_model_beaks > 0):
    if (MODEL["beaks"] == "unknown"):
      log(f"script couldn't detect the _number of beaks_, but user set - {input_model_beaks}; will follow user's choice", "log")
    elif (MODEL["beaks"] == input_model_beaks):
      log(f"script has detected the following _number of beaks_ - {MODEL['beaks']}, and user picked the same _number of beaks_ too")
    elif (MODEL["beaks"] != input_model_beaks):
      log(f"script has detected the following _number of beaks_ - {MODEL['beaks']}, but user picked - {input_model_beaks}; will follow user's choice", "log")
    MODEL["beaks"] = input_model_beaks
  if (MODEL["beaks"] == "unknown"):
    log("script couldn't detect the _number of beaks_ and user didn't set it either; will use 13B and hope for the best", "bad")
    MODEL["beaks"] = 13
  #extra checks for beaks
  if (MODEL["beaks"] == 0):
    log(f"script has detected that model is {MODEL['beaks']}b - which is probably a parsing mistake, or some input issue", "bad")
  #I couldn't refuse
  elif (MODEL["beaks"] == 69):
    log(f"script has detected that model is {MODEL['beaks']}b - nice", "pony")
  elif (MODEL["beaks"] < 13):
    log(f"script has detected that model is {MODEL['beaks']}b - less than 13b; the max context can go higher than 8192 tokens and better quality models can be used", "log")
  elif (MODEL["beaks"] > 20):
    log(f"script has detected that model is {MODEL['beaks']}b - more than 20b; it will most likely not load in Google Colab or will load in a tiny context", "bad")
  elif (MODEL["beaks"] != 13):
    log(f"script has detected that model is {MODEL['beaks']}b - more than 13b; the max context shall be set lower than 4096 tokens, or lower quality models shall be used", "log")


  ########
  #quantz tests
  #seems it only relevant for GGML / GGUF - will filter all other formats
  if (MODEL["format"] in ["ggml", "gguf"]):
    if (input_model_quantz and input_model_quantz != "autodetect"):
      if (MODEL["quantz"] == "unknown"):
        log(f"script couldn't detect the _number of quantz_, but user set - {input_model_quantz}; will follow user's choice", "log")
      elif (MODEL["quantz"] == input_model_quantz):
        log(f"script has detected the following _number of quantz_ - {MODEL['quantz']}, and user picked the same _number of quantz_ too")
      elif (MODEL["quantz"] != input_model_quantz):
        log(f"script has detected the following _number of quantz_ - {MODEL['quantz']}, but user picked - {input_model_quantz}; will follow user's choice", "log")
      MODEL["quantz"], MODEL["quantz_num"] = input_model_quantz, int(re.search(r"[qf](\d+)", input_model_quantz).group(1))
    if (MODEL["quantz"] == "unknown"):
      log("script couldn't detect the _number of quantz_ and user didn't set it either; will use 'q4_k_m' and hope for the best", "bad")
      MODEL["quantz"], MODEL["quantz_num"] = "q4_k_m", 4
    #extra quantz tests
    #give instructions/recommendation on number of beaks vs quantz
    if (MODEL['beaks'] == 13):
      if (MODEL["quantz_num"] < 4):
        log(f"model has {MODEL['quantz_num']} quantz and {MODEL['beaks']}b - Colab can offer more; pick a better model", "log")
      elif (MODEL["quantz_num"] <= 4):
        log(f"model has {MODEL['quantz_num']} quantz and {MODEL['beaks']}b - Colab will work well and higher context is available")
      elif (MODEL["quantz_num"] <= 5):
        log(f"model has {MODEL['quantz_num']} quantz and {MODEL['beaks']}b - Colab will work alright but higher context might not available, try 6-quantz tho!")
      elif (MODEL["quantz_num"] <= 6):
        log(f"model has {MODEL['quantz_num']} quantz and {MODEL['beaks']}b - Colab will work alright but higher context might not available")
      elif (MODEL["quantz_num"] > 6):
        log(f"model has {MODEL['quantz_num']} quantz and {MODEL['beaks']}b - Colab will will not work with it; pick a lower model", "bad")
    if (MODEL['beaks'] < 13):
      if (MODEL["quantz_num"] < 4):
        log(f"model has {MODEL['quantz_num']} quantz and {MODEL['beaks']}b - Colab can offer more; pick a better model", "log")
      elif (MODEL["quantz_num"] <= 5):
        log(f"model has {MODEL['quantz_num']} quantz and {MODEL['beaks']}b - Colab will work well and higher context is available")
      elif (MODEL["quantz_num"] <= 6):
        log(f"model has {MODEL['quantz_num']} quantz and {MODEL['beaks']}b - Colab will work alright but higher context might not available")
      elif (MODEL["quantz_num"] > 6):
        log(f"model has {MODEL['quantz_num']} quantz and {MODEL['beaks']}b - Colab will work bad and probably only on low <4096 context and honestly there is no need to use 6+ quant models even with low-beaks; pick a lower model", "log")
    if (MODEL['beaks'] > 13):
      if (MODEL["quantz_num"] < 4):
        log(f"model has {MODEL['quantz_num']} quantz and {MODEL['beaks']}b - Colab will work alright (I guess) but higher context might not available")
      elif (MODEL["quantz_num"] <= 5):
        log(f"model has {MODEL['quantz_num']} quantz and {MODEL['beaks']}b - Colab will may work but bad and probably only on low <4096 context", "bad")
      elif (MODEL["quantz_num"] >= 6):
        log(f"model has {MODEL['quantz_num']} quantz and {MODEL['beaks']}b - Colab will not work with that stuff; pick a lower model", "bad")
    #previous steps should have removed/renamed that thing, but if still appears then auto-detection failed because of reasons, need to inform user
    if (MODEL["format"] in ["ggml", "gguf"] and MODEL["filename"] == "adapter_model.bin"):
      log("script could not load filename properly - very likely you provided a wrong link. for GGUF/GGML models you must link to the exact file, not to general repo/directory", "bad")


  ########
  #bits tests
  if (MODEL["format"] == "exl2"):
    if (input_model_bits and input_model_bits > 0.0):
      if (MODEL["bits"] == "unknown"):
        log(f"script couldn't detect the _number of bits_, but user set - {input_model_bits}; will follow user's choice", "log")
      elif (MODEL["bits"] == input_model_bits):
        log(f"script has detected the following _number of bits_ - {MODEL['bits']}, and user picked the same _number of bits_ too")
      elif (MODEL["bits"] != input_model_bits):
        log(f"script has detected the following _number of bits_ - {MODEL['bits']}, but user picked - {input_model_bits}; will follow user's choice", "log")
      MODEL["bits"] = input_model_bits
    if (MODEL["bits"] == "unknown"):
      log("script couldn't detect the _number of bits_ and user didn't set it either; will use 5.33 and hope for the best", "bad")
      MODEL["bits"] = 5.33
    #give instructions/recommendation on number of bits vs quantz
    if (MODEL["bits"] <= 4):
      log(f"model has {MODEL['bits']} bits - Colab can easily run ~5 bits models; consider a better model")
    elif (MODEL["bits"] <= 5):
      log(f"model has {MODEL['bits']} bits - Colab may struggle to run it with high context. try to use 6144-6656 context")
    elif (MODEL["bits"] <= 6):
      log(f"model has {MODEL['bits']} bits - Colab will struggle to run it with default context. try to set to 4096 or lower", "log")
    else:
      log(f"model has {MODEL['bits']} bits - Colab either will not launch at all or in very low context", "bad")


  ########
  #etc tests/notes
  if (input_kobold_usecpu and MODEL["backend"] == "koboldcpp"):
    log("user launched koboldcpp in CPU-only mode. the performance will be terribly slow", "bad")
  if (input_ooba_logs):
    log("user launched oobabooga with --verbose flag; console will store user's logs now")
  if (input_ooba_cfg):
    log("user launched oobabooga with --cfg-cache flag for negative prompt; the VRAM usage has been doubled! very likely you can run only in 4096 context max", "log")
    if (MODEL["backend"] not in ["exllama_hf", "llamacpp_hf"]):
      log(f"user activated negative cache but uses loader that doesn't support --cfg-cache - {MODEL['backend']}! use exllama_hf or llamacpp_hf", "bad")
  if (input_ooba_gradio and MODEL["backend"] != "koboldcpp"):
    log("user launched oobabooga in Gradio mode. you can now click on*.gradio.live link and open oobabooga backend in browser")
    if (not input_ooba_gradio_name):
      log("user launched oobabooga in Gradio mode but didn't set his ACCOUNT name; security risk", "bad")
    if (input_ooba_gradio_name == "anon"):
      log("user launched oobabooga in Gradio mode but didn't change his ACCOUNT name; security risk", "log")
    if (not input_ooba_gradio_pw):
      log("user launched oobabooga in Gradio mode but didn't set his PASSWORD; security risk", "bad")
    if (input_ooba_gradio_pw == "PlapPlap1234"):
      log("user launched oobabooga in Gradio mode but didn't change his PASSWORD; security risk", "log")
    #it really doesn't matter t-b-h
    if (input_ooba_gradio_pw in ["password", "pass", "pw", "qwerty", "1234"]):
      log(f">password: {input_ooba_gradio_pw}", "green")
      log(f">/g/ - Techology", "green")
      log(f"anon, I...")
  if (input_ponies):
    log("\n::: Colab is magic :::\n", "pony") #:3

def proc_model_context(elem):
  #here we calculate the about-right* max context for our models. I didn't want to create dictionaries or complex formulas; prefer having everything at glance...
  #...but then went overboard and now don't feel like rewriting it
  global MODEL

  def get_cntx_base(format, quantz, bits, beaks):
    def get_gptq_ctx():
      #for GPTQ models we just return 7168. it is the best value for them
      return 7168

    def get_exl2_ctx():
      #for EXL2 models we return value based on number of bits, and then correct it based on number of beaks
      if bits <= 4.0:
        x = 7680
      elif bits <= 5.0:
        x = 6656
      elif bits <= 6.0:
        x = 4096
      elif bits <= 8.0:
        x = 2048
      elif bits <= 9.0:
        x = 1024
      else:
        x = 4096
      if (beaks < 13):
        x = x + (8192 / x * 64) * (13 - beaks)
      if (beaks > 13):
        x = x - ((beaks - 13) * 256)
      return x

    def get_gguf_ctx():
      #for GGUF/GGML models we return value based on number of quantz, and then correct it based on number of beaks
      map = {
        2: 8192,
        3: 7168,
        4: 6144,
        5: 5632,
        6: 4096,
        8: 2048,
        16: 1024
      }
      x = map[quantz]
      if (beaks < 13):
        x = x + (8192 / x * 64) * (13 - beaks)
      if (beaks > 13):
        x = x - ((beaks - 13) * 256)
      return x

    def get_gptq_awq():
      #same as GPTQ
      return 7168

    cntx_base = {
      "gptq": get_gptq_ctx,
      "exl2": get_exl2_ctx,
      "gguf": get_gguf_ctx,
      "ggml": get_gguf_ctx,
      "awq": get_gptq_awq
    }
    return cntx_base[format]()

  def get_cntx_per_beaks(beaks, number):
    ctx = number
    if (beaks == 20):
        ctx = number / 3
    elif (beaks == 7):
        ctx =  number * 1.8
    elif (beaks > 13):
        #interpolated
        ctx =  number / (1 + (-0.0957) * (beaks - 13))
    elif (beaks < 13):
        ctx =  number * (1.8 + (-0.25) * (beaks - 7))
    return math.ceil(ctx / 512) * 512

  def get_alpha(number):
    #I spent too much time on that...
    if (number < 4096):
      return 1.0
    elif (number > 8192):
      return 2.9

    alpha_map = {
      "4096": "1.0",
      "4608": "1.17",
      "5120": "1.25",
      "5632": "1.56",
      "6144": "1.79",
      "6656": "2.01",
      "7168": "2.28",
      "7680": "2.60",
      "8192": "2.90"
    }
    #round-down our context to the nearest 512-value before throwing it into map
    number = math.ceil(number / 512) * 512
    return float(alpha_map[str(number)])

  def assign_context():
    if (input_model_free_context > 0):
      log(f"...[context] user set context to {input_model_free_context}. will assign that value and will not pick max context automatically", "log")
      return input_model_free_context
    elif (input_model_context > 0 and input_model_free_context == 0):
      log(f"...[context] user set context to {input_model_context}. will assign that value and will not pick max context automatically", "log")
      return input_model_context
    else:
      log(f"...[context] user didn't set context. will calculate max context automatically")
      #we are doing auto-calculation of context in two steps: first we get the based max value based on models' properties
      cntx_detected = get_cntx_base(MODEL["format"], MODEL["quantz_num"], MODEL["bits"], MODEL["beaks"])
      #then increase/decrease that value based on number of beaks:
      if (cntx_detected > 0):
        cntx_detected = get_cntx_per_beaks(MODEL["beaks"], cntx_detected)
      #and if we managed to get a negative number, then return 0 because kek
      else:
        cntx_detected = 0

      #koboldcpp works only with context of specific size, so we must take the context we obtained and change it to the nearest lowest value (4444 -> 4096, 5555 -> 4096, 6133 -> 4096)
      #@todo: rewrite
      if (MODEL["backend"] == "koboldcpp"):
        koboldcpp_nums = [512, 1024, 2048, 3072, 4096, 6144, 8192, 12288, 16384]
        cntx_detected = min(filter(lambda n: n <= cntx_detected, koboldcpp_nums), key=lambda n: abs(cntx_detected - n))

      log(f"::::::::::::::::::::::::::::::::::::::::::::::::::::::::::::::::::::::::::::::::::::::::::::::", "log")
      log(f"::: notebook automatically calculated the about-right* CONTEXT for this model:")
      log(f"::: {cntx_detected}", "log")
      log(f"::: if model does not work properly with that context (CUDA error) then try lower it by 512")
      log(f"::: it is only an approximate value - test and report back. especially with non-13b models")
      log(f"::::::::::::::::::::::::::::::::::::::::::::::::::::::::::::::::::::::::::::::::::::::::::::::", "log")
      return cntx_detected

  def assign_alpha():
    if (input_model_free_alpha_value > 0):
      return input_model_free_alpha_value
    return get_alpha(MODEL["context_value"])

  MODEL["context_value"] = assign_context()
  MODEL["context_alpha"] = assign_alpha()


def update_llama_stats(link_pointer):
  #code for publishing analytics into @kalomaze's spreadsheet. copy-paste from his Colab, only changed varibles
  #and added extra code to submit once per Colab instance
  if (os.path.exists(PATH['sheet_done'])):
    log("...[analytics] already shared analytics for that Colab isntance; bail and continue the script")
    return False

  # Initialize gspread
  scope = [
    'https://www.googleapis.com/auth/spreadsheets',
    'https://www.googleapis.com/auth/drive.file',
    'https://www.googleapis.com/auth/drive'
  ]

  #os.makedirs(PATH['kobold'], exist_ok=True)
  !wget -q https://cdn.discordapp.com/attachments/945486970883285045/1114717554481569802/peppy-generator-388800-07722f17a188.json -O {PATH["sheet_start"]}
  config_path = PATH['sheet_start']

  if os.path.exists(config_path):
    # File exists, proceed with creation of creds and client
    creds = Credentials.from_service_account_file(config_path, scopes=scope)
    client = gspread.authorize(creds)
  else:
    # File does not exist, print message and skip creation of creds and client
    log("...[analytics] cannot share stats because credential file missing; bail and continue the script", "log")
    return False  # Exit the script if the credentials are missing

  # Open the Google Sheet
  book = client.open("LlamaStats")
  sheet = book.get_worksheet(0)  # get the first sheet

  def calculate_md5(file_path):
    hash_md5 = hashlib.md5()
    with open(file_path, "rb") as f:
      for chunk in iter(lambda: f.read(4096), b""):
        hash_md5.update(chunk)
    return hash_md5.hexdigest()

  DownloadedModel_name = os.path.basename(link_pointer)
  DownloadedModel_hash = calculate_md5(MODEL["path_pointer"])

  colA_values = sheet.col_values(1)
  colB_values = sheet.col_values(2)
  colC_values = sheet.col_values(3)

  update_idx = -1

  for idx in range(len(colA_values)):
    if colA_values[idx] == DownloadedModel_name and idx < len(colB_values) and colB_values[idx] == DownloadedModel_hash:
      update_idx = idx + 1
      break

  if update_idx == -1:
    update_idx = len(colA_values) + 1

  current_count = colC_values[update_idx - 1] if update_idx <= len(colC_values) else ''
  if current_count.isdigit():
    new_count = str(int(current_count) + 1)
  else:
    new_count = '1'

  # Batch update to Google Sheets
  cell_list = [
    gspread.models.Cell(update_idx, 1, DownloadedModel_name),
    gspread.models.Cell(update_idx, 2, DownloadedModel_hash),
    gspread.models.Cell(update_idx, 3, new_count),
    gspread.models.Cell(update_idx, 4, link_pointer)
  ]
  sheet.update_cells(cell_list)
  log("...[analytics] updating the value in google spreadsheet", "log")
  os.mknod(PATH['sheet_done'])


###################################
### DOWNLOADER - LoRA
###################################
def check_if_exists_and_download_lora():
  global LORA

  def lora_parse_link(link):
    parts = clean_link(link).split("/")
    protocol = get_element(parts, 0, "https:")
    empty = get_element(parts, 1, "")
    domain = get_element(parts, 2, "huggingface.co")
    author = get_element(parts, 3, "Undi95")
    repo = get_element(parts, 4, "Storytelling-v2-13B-lora") # :3
    tree = get_element(parts, 5, "tree")
    branch = get_element(parts, 6, "main")
    filename = get_element(parts, 7, "adapter_model.bin")

    link_main = f"https://huggingface.co/{author}/{repo}"
    path_pointer = f"{PATH['temp']}{repo}"

    if (os.path.exists(path_pointer) and len(os.listdir(path_pointer)) > 0):
      log(f"...[LoRA] LoRA {repo} is already downloaded")
    else:
      log(f"...[LoRA] LoRA {repo} is NOT present in system, downloading", "log")
      download_git(link_main, path_pointer, branch)

    #for koboldcpp we need provide full path to LoRAs' bin, for oobabooga we need to provide only relative path to folder with bin and json
    if (MODEL["backend"] != "koboldcpp"):
      return repo
    else:
      bin_files = [f for f in os.listdir(path_pointer) if f.endswith('.bin')]
      if bin_files:
        return f"{PATH['temp']}{repo}/{bin_files[0]}"
      else:
        log(f"...[LoRA] cannot find LoRA {repo}'s bin, will return repo instead", "log")
        return repo

  def split_string(text):
      if text:
          return [s.strip() for s in text.replace('"', '').replace("'", '').split(',') if s.strip()]
      return []

  list_lora_pony = {
    "none": [],
    "FIMFarchive-v1": ["https://huggingface.co/hfmlp/llama-2-13b-pny-3e"],
    "desu-/mlp/-v1": ["https://huggingface.co/hfmlp/llama-2-13b-mlpposts-20epl-3e"],
    "both": ["https://huggingface.co/hfmlp/llama-2-13b-pny-3e", "https://huggingface.co/hfmlp/llama-2-13b-mlpposts-20epl-3e"] #unavailable but coded
  }

  LORA = list_lora_pony[input_lora_pony] + split_string(input_lora_string)
  LORA = [x for x in LORA if isinstance(x, str) and x != '']

  if not LORA:
    log("...[LoRA] LoRAs are not specified, will not apply")
  else:
    log("...[LoRA] LoRAs are specified, will process them now")
    for i in range(len(LORA)):
      log(f"...[LoRA] processing LoRA {LORA[i]}")
      LORA[i] = lora_parse_link(LORA[i])

  LORA = ' '.join(LORA)
  return LORA


###################################
### START
###################################
log("::: NOTEBOOK STARTED :::", "sect")

#create two folders: /content/colabMain/ for backend and /content/colabTemp/ for models and LoRAs
os.chdir("/content/")
os.makedirs(PATH["main"], exist_ok=True)
os.makedirs(PATH["temp"], exist_ok=True)

#put ponies into thread
thread_pony = threading.Thread(target=ponies_set)
thread_pony.start()

#download aria via thread
thread_aria = threading.Thread(target=depend_aria)
thread_aria.start()

#parsing model via thread
thread_model_process = threading.Thread(target=parse_link, args=({input_model_string}))
thread_model_process.start()
thread_model_process.join()
proc_model_details(MODEL)
proc_model_notes(MODEL)
proc_model_context(MODEL)

thread_aria.join() #wait until aria is done


###################################
### DOWNLOAD BACKEND, MODEL, LORA
###################################
log("::: DOWNLOAD BACKEND, MODEL, LORA :::", "sect")

if (MODEL["backend"] == "koboldcpp"):
  log("...[backend] processing the backend: kobold.cpp")
  thread_launch_kobold_cloudflare = threading.Thread(target=depend_kobold_cloudflare)
  thread_launch_kobold_cloudflare.start()
  thread_download_backend = threading.Thread(target=check_if_exists_and_download_kobold)
else:
  log("...[backend] processing the backend: oobabooga")
  thread_download_backend = threading.Thread(target=check_if_exists_and_download_ooba)
thread_download_backend.start()

log(f"...[model] processing the model: {input_model_string}")
thread_download_model = threading.Thread(target=check_if_exists_and_download_model)
thread_download_model.start()

thread_download_model.join() #we don't start LoRAs download until model is done first
if (input_analytics and MODEL["format"] == "gguf"):
    thread_model_analytics = threading.Thread(target=update_llama_stats, args=({MODEL["link_pointer"]}))
    thread_model_analytics.start()

log(f"...[LoRA] processing LoRA")
thread_download_lora = threading.Thread(target=check_if_exists_and_download_lora)
thread_download_lora.start()

thread_download_backend.join() #wait until backend is done
thread_download_lora.join() #wait until LoRAs (and thys Model) is done


###################################
### PARAMETERS
###################################
log("::: LAUNCHING BACKEND :::", "sect")
input_ponies=False
cmd_params = set()
if (MODEL["backend"] == "koboldcpp"):
  cmd_params.add(f"--model {MODEL['path_pointer']}")
  cmd_params.add(f"--hordeconfig {MODEL['repo']}")
  cmd_params.add(f"--context {MODEL['context_value']}")

  if (LORA):
    cmd_params.add(f"--lora {LORA}")

  #--stream doesn't support in 1.46+ so that check exists
  if (input_kobold_stream and input_kobold_version in ["1.44.2", "1.43"]):
    cmd_params.add("--stream")

  if (input_kobold_smartcontext):
    cmd_params.add("--smartcontext")

  if (not input_kobold_usecpu):
    cmd_params.add(f"--highpriority --threads 2 --usecublas normal 0 mmq --gpulayers {input_flag_gpulayers}")
  else:
    cmd_params.add(f"--highpriority --threads 2 --usemlock")

  thread_launch_kobold_cloudflare.join()
  log("Cloudflare tunnel was created, here is the link:", "info")
  !cat {PATH["cloud_nohup"]}

  cmd = f"python {PATH['kobold_start']} {' '.join(cmd_params)}"

else:
  cmd_params.add(f"--loader {MODEL['backend']}")
  cmd_params.add("--api --public-api")
  cmd_params.add(f"--model-dir {PATH['temp']}")
  cmd_params.add(f"--lora-dir {PATH['temp']}")

  cmd_params.add(f"--model {MODEL['pointer']}")

  if (LORA):
    cmd_params.add(f"--lora {LORA}")

  if (MODEL["format"] == "gguf" or MODEL["format"] == "ggml"):
    #@todo: --threads-batch unsupported now because of flash-attention, revisit later --threads-batch 4
    cmd_params.add(f"--threads 2 --n_ctx {MODEL['context_value']} --n-gpu-layers {input_flag_gpulayers} --mul_mat_q")
  else:
    #we had to set rope_freq_base to 0 to force the usage of alpha_value instead; otherwise Ooba will use rope_freq_base by default and not scale properely
    cmd_params.add(f"--max_seq_len {MODEL['context_value']} --alpha_value {MODEL['context_alpha']} --rope_freq_base 0")

  if (input_ooba_logs):
    cmd_params.add("--verbose")

  if (input_ooba_cfg):
    cmd_params.add("--cfg-cache")

  if (input_ooba_gradio):
    cmd_params.add(f"--share --gradio-auth {input_ooba_gradio_name}:{input_ooba_gradio_pw}")

  #yes, you have to launch oobabooga from INSIDE the folder, or otherwise you will get the error: get KeyError: 'cai-chat'
  #https://github.com/oobabooga/text-generation-webui/issues/3932
  #kek and lul I know
  #
  #disregard 'You are running ExLlamaV2 without flash-attention' instruction - that stuff breaks Colab
  %cd {PATH["ooba"]}
  cmd = f"python server.py {' '.join(cmd_params)}"

log("\nbackend is launched with the following flags:")
log(cmd, "info")
!$cmd


#snippet when I need to update tar archive, don't mind
#
#kobold_folder = '/content/colabMain'
#with tarfile.open('koboldcpp.tar.gz', 'w:gz') as tar:
# for file in os.listdir(kobold_folder):
#   tar.add(os.path.join(kobold_folder, file), arcname=file)